In [5]:
conda install pandana


Note: you may need to restart the kernel to use updated packages.



CondaSSLError: OpenSSL appears to be unavailable on this machine. OpenSSL is required to
download and install packages.

Exception: HTTPSConnectionPool(host='repo.anaconda.com', port=443): Max retries exceeded with url: /pkgs/main/win-64/current_repodata.json (Caused by SSLError("Can't connect to HTTPS URL because the SSL module is not available."))




In [4]:
import pandana
import osmnx as ox
import geopandas as gpd
from sqlalchemy import create_engine
import psycopg2
import pandas as pd
import geoalchemy2
import numpy as np

ModuleNotFoundError: No module named 'pandana'

In [3]:
# функция для чтения того, что получили в запросе
def select_pg(sql, geom):
    return gpd.read_postgis(sql, engine, geom_col = geom, crs = 3857)

engine = create_engine('postgresql+psycopg2://kb_geo:kYZQK90yvE8aNi54ELINc0yJ1gu6wo7h@\
db03.cluster.strlk.ru/kb_geo')

In [4]:
#достаем фотографии из базы
sql = "SELECT * from strelka_data_russia.vk_photo_2022_meta join region_msk_spb_ on st_intersects(strelka_data_russia.vk_photo_2022_meta.geom,region_msk_spb_.geom"
photo = select_pg(sql, 'geom')
photo = photo.to_crs(3857)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "c:\Users\apikuleva\Anaconda3\lib\site-packages\sqlalchemy\engine\base.py", line 1819, in _execute_context
    self.dialect.do_execute(
  File "c:\Users\apikuleva\Anaconda3\lib\site-packages\sqlalchemy\engine\default.py", line 732, in do_execute
    cursor.execute(statement, parameters)
psycopg2.errors.SyntaxError: syntax error at end of input
LINE 1: ...lka_data_russia.vk_photo_2022_meta.geom,region_msk_spb_.geom
                                                                       ^


The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "c:\Users\apikuleva\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py", line 3457, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "C:\Users\apikuleva\AppData\Local\Temp\ipykernel_6092\1598713678.py", line 3, in <module>
    photo = select_pg(sql, 'geom')
  File "C:\Users\apikuleva\AppData\Local\Temp\ipykernel_6092\

TypeError: object of type 'NoneType' has no len()

In [7]:
#аттракторы
sql = "SELECT geom, id FROM public.buffered "
attractor = select_pg(sql, 'geom')
attractor = attractor.to_crs(3857)

In [8]:
sql = "SELECT * FROM public.photo_in_buffer_new "
photo_in_buffer = select_pg(sql, 'geom')
photo_in_buffer = photo_in_buffer.to_crs(3857)
photo_in_buffer = photo_in_buffer.sort_values(['owner_id','date_time'])


In [117]:
edge_graph_moscow_spb = "SELECT * FROM public.all_edge_msk_spb_new "
node_graph_moscow_spb = "SELECT * FROM public.all_node_msk_spb_new"

node_graph = select_pg(node_graph_moscow_spb, 'geom')
edge_graph = select_pg(edge_graph_moscow_spb, 'geometry')

node_graph['lng']= node_graph['geom'].to_crs(4326).x
node_graph['lat']= node_graph['geom'].to_crs(4326).y


edge_graph = edge_graph[edge_graph['source'].isin(node_graph['id']) & edge_graph['target'].isin(node_graph['id'])]
node_graph.set_index('id', inplace= True)


# create network with pandana
graph = pandana.Network(node_graph['lng'], node_graph['lat'], 
                          edge_graph['source'], edge_graph['target'], edge_graph[['distant']])



In [111]:
# Подсчет количества строк с NaN значениями
nan_rows = node_graph_main.isna().sum().sum()

print("Количество строк со значением NaN: ", nan_rows)

Количество строк со значением NaN:  0


In [100]:
edge_graph_main = edge_graph_main.dropna()

In [109]:
node_graph_main = node_graph_main.reset_index()

In [ ]:
node_graph_main = node_graph[['lng', 'lat']]
node_graph_main = node_graph_main.dropna()

In [112]:
edge_graph_main['source'] = edge_graph_main['source'].astype(int)
node_graph_main['lng'] = node_graph_main['lng'].astype(float)
node_graph_main['lat'] = node_graph_main['lat'].astype(float)
edge_graph_main['target'] = edge_graph_main['target'].astype(int)
edge_graph_main['speed_kph'] = edge_graph_main['speed_kph'].astype(int)

c:\Users\apikuleva\Anaconda3\lib\site-packages\geopandas\geodataframe.py:1443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [127]:
# photo_in_buffer
photo_in_buffer['lng']= photo_in_buffer['geom'].to_crs(crs=4326).x
photo_in_buffer['lat']= photo_in_buffer['geom'].to_crs(crs=4326).y

photo_in_buffer['lat_next'] = photo_in_buffer.lat.shift(-1)
photo_in_buffer['lng_next'] = photo_in_buffer.lng.shift(-1)

photo_in_buffer.drop(photo_in_buffer.tail(1).index,inplace=True) # drop last n rows 

origin_nodes = graph.get_node_ids(photo_in_buffer.lng, photo_in_buffer.lat).values
dests_nodes = graph.get_node_ids(photo_in_buffer.lng_next, photo_in_buffer.lat_next).values

In [146]:
photo_in_buffer['origin_nodes'] = graph.get_node_ids(photo_in_buffer.lng, photo_in_buffer.lat)
photo_in_buffer['dests_nodes'] = graph.get_node_ids(photo_in_buffer.lng_next, photo_in_buffer.lat_next)

In [128]:
origin_dest_nodes = zip(origin_nodes, dests_nodes)
origin_dest_nodes_drop = list(set(origin_dest_nodes))

In [137]:
print(origin_dest_nodes_drop)

[(988190, 360258), (1319214, 1318882), (360379, 380841), (994351, 1034423), (350250, 2006164), (6834, 1595972), (1038429, 1063342), (1594385, 356449), (1095752, 2988936), (1076619, 1055230), (1045614, 1045575), (400926, 400925), (1952896, 1606949), (1315186, 1314876), (1053290, 416175), (361984, 16107), (358579, 1003474), (964795, 965079), (2000480, 15176), (1022541, 1033851), (16745, 366848), (1605861, 1604940), (401823, 401823), (1607101, 16523), (1867195, 358579), (370449, 358528), (1958106, 1870978), (2001975, 2001975), (1961804, 991003), (964848, 965090), (1315575, 1314809), (1609343, 1609345), (1035357, 1035177), (1022133, 1022133), (393498, 17129), (384211, 401426), (348316, 360258), (1606674, 1004820), (1021594, 1021855), (400937, 381435), (1068125, 1068125), (998004, 998120), (1034365, 1034365), (420572, 1079342), (1952123, 2990691), (380704, 380907), (998396, 987798), (1963440, 348317), (369506, 980058), (391816, 392354), (1318595, 1318594), (1315541, 1315575), (2006300, 3502

In [133]:
nodes = pd.concat([origin_nodes, dests_nodes], axis= 1)
# unique_rows_count = len(nodes.groupby(['origin_nodes', 'dests_nodes']).size())
df_with_count = nodes.groupby(['origin_nodes', 'dests_nodes']).size().reset_index(name='count')

TypeError: cannot concatenate object of type '<class 'numpy.ndarray'>'; only Series and DataFrame objs are valid

In [143]:
photo_in_buffer.to_postgis('photo_in_buffer_path', engine, if_exists='replace')

In [13]:
print(len(origin_nodes))

955428


In [129]:
nodes_list_2 = []
origin_nodes_list = []
dests_nodes_list = []

for i, k in origin_dest_nodes_drop:

    p = graph.shortest_path(i,k)
    nodes_list_2.append(p)
    origin_nodes_list.append(i)
    dests_nodes_list.append(k)
    

In [130]:
path = pd.DataFrame(list(zip(nodes_list_2, origin_nodes_list, dests_nodes_list)))
path = path.explode(0)
path[0] = pd.to_numeric(path[0], downcast='integer')
path.to_sql('path_msk_spb_main', engine, if_exists='replace')

212

In [131]:
path = pd.DataFrame(list(zip(nodes_list_2, origin_nodes_list, dests_nodes_list)))
path.to_csv('path2.csv')